In [1]:
# Install dependencies, if necessary. 

import sys
!{sys.executable} -m pip install numpy -q
!{sys.executable} -m pip install pandas -q
!{sys.executable} -m pip install matplotlib -q
!{sys.executable} -m pip install seaborn -q
!{sys.executable} -m pip install faker -q

In [2]:
#general purpose
import os
import urllib3
import re
from tempfile import NamedTemporaryFile
from collections import OrderedDict
import pandas as pd
import numpy as np

#Library to generate synthetic data
from faker import Faker
from faker.providers import DynamicProvider

#Viz stuff
import matplotlib.pyplot as plt
import seaborn as sns
from matplotlib.patches import Patch
import matplotlib.pyplot as plt
import matplotlib.font_manager as fm

%matplotlib inline
%config InlineBackend.figure_format='retina'

## Import Fonts

In [3]:
class Fonts_Library():
    """Fonts_Library Class that manages the fonts and their associated temporary file paths

    Dictionary-based

    get_google_font(url: str): function that saves a font from google fonts github temporary and returns the matplotlib fontProperties object

        Args:
            url (str): string of github-permalink to the *.ttf file of the desired google fonts

        Returns:
            _type_: matplotlib.fontmanager.FontProperties

    list_fonts(): function to list the loaded fonts (keys in dict)

        Args: None
        
        Returns: list of strings

    del_font(key: string): function to remove the specified font

        Args: key of the font to be removed
        Returns: None

    clear_library(): function to clear the library

    """

    def __getitem__(self, key):
        return self.__dict__[key]

    def __contains__(self, key):
        return key in self.__dict__

    def __len__(self):
        return len(self.__dict__)
    
    def __repr__(self):
        return repr(self.__dict__)

    def get_google_font(self, url):

        if not os.path.exists('./temp/'):
            os.makedirs('./temp/')

        title = re.search('[A-Z].+', url).group()[:-4].replace('-','_')
        
        if title not in self.__dict__:
            http = urllib3.PoolManager()
            url = f'{url}?raw=true'
            response = http.urlopen('GET', url)
            f = NamedTemporaryFile(delete=False, suffix='.ttf', dir='./temp/')
            f.write(response.data)
            f.close()
            font = fm.FontProperties(fname=f.name)
            self.__dict__[title] = font
        else:
            print('Font is already installed')
    
    def list_fonts(self):
        return list(self.__dict__.keys())
    
    def clear_library(self):
        tmp_files = [v.get_file() for v in self.__dict__.values()]
        list(map(os.unlink,tmp_files))
        os.rmdir('./temp')
        del self.__dict__

    def del_font(self, key):
        os.unlink(self.__dict__[key].get_file())
        del self.__dict__[key]

In [4]:
# Import the required fonts

font_library = Fonts_Library()
urls = ['https://github.com/google/fonts/blob/990be3ed8f77e31c26bf07b148d6a74b8e6241cf/apache/roboto/static/RobotoCondensed-Light.ttf',
         'https://github.com/google/fonts/blob/990be3ed8f77e31c26bf07b148d6a74b8e6241cf/apache/roboto/static/Roboto-Regular.ttf',
         'https://github.com/google/fonts/blob/990be3ed8f77e31c26bf07b148d6a74b8e6241cf/apache/roboto/static/Roboto-Black.ttf'
]

for url in urls:
    font_library.get_google_font(url)

font_library.list_fonts()

['RobotoCondensed_Light', 'Roboto_Regular', 'Roboto_Black']

## Generate synthetic data for Visualization

In [5]:
fake = Faker('de_DE')
fake.name()

'Irina Kitzmann'

In [6]:

#create an own provider
medical_professions_provider = DynamicProvider(
     provider_name="role",
     elements=OrderedDict([('Data Analyst', 0.2),
               ('Data Engineer', 0.1),
               ('Database Administrator',0.1),
               ('Machine Learning Engineer', 0.05),
               ('Data Scientist', 0.15),
               ('Data Architect', 0.05),
               ('Statistician', 0.05),
               ('Data and Analytics Manager',0.05),
               ('Business Intelligence Developer',0.1),
               ('Computer Vision Engineer', 0.05),
               ('Natural Language Processing Engineer',0.05)
               ])
)

fake.add_provider(medical_professions_provider)
# now you can use:
[fake.role() for _ in range(10)]

['Computer Vision Engineer',
 'Data Analyst',
 'Data and Analytics Manager',
 'Data Analyst',
 'Computer Vision Engineer',
 'Data Scientist',
 'Database Administrator',
 'Data Analyst',
 'Data Engineer',
 'Business Intelligence Developer']

In [7]:
def fake_profiles(length: int):
    """fake_profiles: function that generates synthetic profiles

    Args:
        length (int): _description_

    Returns: pd.DataFrame containing name, start, end and role columns
    """

    data = pd.DataFrame()
    for i in range (0, length):
        data.loc[i, 'name'] = fake.name()
        data.loc[i, 'start'] = fake.random_int(min = 1943, max = 2023)
        data.loc[i, 'end'] = data.loc[i, 'start'] + fake.random_int(min = 1, max = 35)
        data.loc[i, 'role'] = fake.role()
    
    data.name = data.name.astype('string')
    data.start = data.start.astype('int')
    data.end = data.end.astype('int')
    data.role = data.role.astype('string')
    data.end = data.end.where(data.end <= 2025, 2025)
    return(data)

In [8]:
df_fake_staff = fake_profiles(100)
df_fake_staff.head()

name  start   end  \
0         Dina Schulz-Fliegner   2012  2025   
1       Timm Sölzer-Neuschäfer   1972  2005   
2             Marlis Roht B.A.   1982  1983   
3         Dr. Gretchen Hermann   2023  2025   
4  Univ.Prof. Sergio Ackermann   1945  1974   

                                   role  
0              Computer Vision Engineer  
1  Natural Language Processing Engineer  
2                          Statistician  
3                        Data Architect  
4       Business Intelligence Developer

In [9]:
df_fake_staff.dtypes

name     string
start     int64
end       int64
role     string
dtype: object

In [10]:
sorted(df_fake_staff['role'].unique())

['Business Intelligence Developer',
 'Computer Vision Engineer',
 'Data Analyst',
 'Data Architect',
 'Data Engineer',
 'Data Scientist',
 'Data and Analytics Manager',
 'Database Administrator',
 'Machine Learning Engineer',
 'Natural Language Processing Engineer',
 'Statistician']

In [11]:
# add abberivations to the dataframe

abbr_dict = { 'Business Intelligence Developer':'BI-DEV',
    'Computer Vision Engineer':'CV-ENG',
    'Data Analyst':'D-AN',
    'Data Architect':'D-AR',
    'Data Engineer':'D-ENG',
    'Data Scientist':'D-SCI',
    'Data and Analytics Manager':'D&A-MNGR',
    'Database Administrator':'DB-ADMIN',
    'Machine Learning Engineer':'ML-ENG',
    'Natural Language Processing Engineer':'NLP-ENG',
    'Statistician':'STAT'
    }
df_fake_staff['abbr'] = df_fake_staff['role'].apply(lambda x: abbr_dict.get(x) if abbr_dict.get(x) != None else x)

In [12]:
df_fake_staff = df_fake_staff.sort_values(by=['start', 'name'], ascending=[True,False]).reset_index(drop=True)
df_fake_staff

name  start   end                             role  \
0              Karsten Wernecke   1943  1971                     Data Analyst   
1            Agathe Gertz B.Sc.   1944  1971                   Data Scientist   
2   Univ.Prof. Sergio Ackermann   1945  1974  Business Intelligence Developer   
3         Johannes Hölzenbecher   1945  1963                     Data Analyst   
4                  Udo Fliegner   1946  1978                     Data Analyst   
..                          ...    ...   ...                              ...   
95           Rosalinde Bohnbach   2022  2025  Business Intelligence Developer   
96         Patrizia Zimmer B.A.   2022  2025                     Statistician   
97       Maxim Wohlgemut B.Eng.   2023  2024        Machine Learning Engineer   
98              Ernst-Otto Karz   2023  2025                   Data Scientist   
99         Dr. Gretchen Hermann   2023  2025                   Data Architect   

      abbr  
0     D-AN  
1    D-SCI  
2   BI-DEV  
3     D-AN  
4     D-AN  
..     ...  
95  BI-DEV  
96    STAT  
97  ML-ENG  
98   D-SCI  
99    D-AR  

[100 rows x 5 columns]

In [13]:
#check for duplicates
df_fake_staff.loc[df_fake_staff.duplicated(subset=['name','role','start','end'],keep=False),:]

Empty DataFrame
Columns: [name, start, end, role, abbr]
Index: []

## Prepare data for visualization

In [14]:
#sort the data frame in such way, that the new data is outside of the visualization

sorted_df = pd.DataFrame(columns=df_fake_staff.columns)
years = df_fake_staff.start.unique().tolist()
up = True
for year in years:
    df_help = df_fake_staff.loc[df_fake_staff.start == year,:].reset_index(drop=True)
    size = df_help.shape[0]
    if (size % 2) == 0:
        rows_top = int(size / 2)
        #rows_bottom = rows_top
    else:
        rows = size / 2
        if up:
            rows_top = int(rows + 0.5)
            #rows_bottom = int(rows - 0.5)
            up = False    
        else:
            rows_top = int(rows - 0.5)
            #rows_bottom = int(rows + 0.5)
            up = True

    #print(f'size: {size}, rows_top: {rows_top}, rows_bottom: {rows_bottom}')

    #df_top = df_help.loc[0,:] if rows_top == 1 else df_help.loc[0:rows_top,:]
    df_top = df_help.loc[:rows_top-1,:]
    df_bottom = df_help.loc[rows_top:,:]

    sorted_df = pd.concat([df_top, sorted_df]).reset_index(drop = True)
    sorted_df = pd.concat([sorted_df, df_bottom]).reset_index(drop = True)

    #print(f'top {df_top.Ganznamen}')
    #print(f'bottom {df_bottom.Ganznamen}')

    #print(sorted_df)
sorted_df

name start   end  \
0           Maxim Wohlgemut B.Eng.  2023  2024   
1               Rosalinde Bohnbach  2022  2025   
2       Dipl.-Ing. Saskia Losekann  2021  2025   
3              Frau Dorina Reising  2020  2025   
4      Prof. Manuela Scheibe B.Sc.  2016  2025   
..                             ...   ...   ...   
95                 Filiz Wohlgemut  2019  2025   
96  Dipl.-Ing. Lutz Conradi B.Eng.  2020  2025   
97            Patrizia Zimmer B.A.  2022  2025   
98                 Ernst-Otto Karz  2023  2025   
99            Dr. Gretchen Hermann  2023  2025   

                                    role     abbr  
0              Machine Learning Engineer   ML-ENG  
1        Business Intelligence Developer   BI-DEV  
2                         Data Scientist    D-SCI  
3               Computer Vision Engineer   CV-ENG  
4   Natural Language Processing Engineer  NLP-ENG  
..                                   ...      ...  
95                        Data Scientist    D-SCI  
96                          Data Analyst     D-AN  
97                          Statistician     STAT  
98                        Data Scientist    D-SCI  
99                        Data Architect     D-AR  

[100 rows x 5 columns]

In [15]:
sorted_df.start.min()

1943

In [16]:
cats_full = sorted_df['role'].unique().tolist()
cats_full.sort()
print(len(cats_full))
cols = sns.color_palette('Blues', len(cats_full))
palette_full = dict(zip(cats_full, cols))
palette_full


11


{'Business Intelligence Developer': (0.9040369088811996,
  0.9429757785467128,
  0.9793310265282583),
 'Computer Vision Engineer': (0.8406920415224913,
  0.9016378316032295,
  0.9586620530565167),
 'Data Analyst': (0.7752402921953095, 0.8583006535947711, 0.9368242983467897),
 'Data Architect': (0.6718954248366014,
  0.8143790849673203,
  0.9006535947712418),
 'Data Engineer': (0.5545098039215688, 0.7564167627835449, 0.8683121876201461),
 'Data Scientist': (0.41708573625528644,
  0.6806305267204922,
  0.8382314494425221),
 'Data and Analytics Manager': (0.31115724721261057,
  0.6082891195693964,
  0.7968935024990389),
 'Database Administrator': (0.21568627450980393,
  0.5294117647058824,
  0.7542483660130719),
 'Machine Learning Engineer': (0.1271049596309112,
  0.4401845444059977,
  0.7074971164936563),
 'Natural Language Processing Engineer': (0.06251441753171857,
  0.35750865051903113,
  0.6429065743944637),
 'Statistician': (0.03137254901960784, 0.2734948096885813, 0.546205305651672

In [17]:
x = np.arange(1940,sorted_df.end.max()+5,0.25)

def generate_array(data, x):
    data['start_comp'] = data['start'].astype(int) - 1940
    data['end_comp'] = data['end'].astype(int) - 1940

    np_ranges = data[['start_comp','end_comp']].to_numpy()
    np_ranges = np_ranges*4
    arr = np.zeros([np_ranges.shape[0], x.shape[0]])
    for i, (a,b) in enumerate(np_ranges):
    # arr[i, a:b+4] = 1 ##old
        if a == b:
            arr[i, a:b+4] = 1
        else:
            arr[i, a:b+4] = 1
    return arr

arr_full = generate_array(sorted_df, x)
print(f'x: {x.shape}\narr: {arr_full.shape}')

x: (360,)
arr: (100, 360)


In [18]:
legend_elements_full = [Patch(facecolor = v, edgecolor='black', label = f'{k} ({abbr_dict.get(k)})') for k,v in palette_full.items()]

In [19]:
fig, ax = plt.subplots(figsize = (230,35))
#plt.rcParams['svg.fonttype'] = 'none'

baseline = 'wiggle' # wiggle, weighted_wiggle , sym or zero

ax.stackplot(x, arr_full, 
             labels = palette_full, 
             colors = [palette_full.get(l) for l in sorted_df['role']], 
             baseline = baseline, 
             edgecolor = 'white', 
             linewidth = 0.5, 
             capstyle = 'round', 
             #hatch = '/',
             zorder = 10
             )

y_help = np.vstack(arr_full)
stack = np.cumsum(y_help, axis=0, dtype=np.promote_types(y_help.dtype, np.float32))

if baseline == 'zero':
        first_line = 0.

elif baseline == 'sym':
    first_line = -np.sum(y_help, 0) * 0.5
    stack += first_line[None, :]

elif baseline == 'wiggle':
    m = y_help.shape[0]
    first_line = (y_help * (m - 0.5 - np.arange(m)[:, None])).sum(0)
    first_line /= -m
    stack += first_line

elif baseline == 'weighted_wiggle':
    total = np.sum(y_help, 0)
    # multiply by 1/total (or zero) to avoid infinities in the division:
    inv_total = np.zeros_like(total)
    mask = total > 0
    inv_total[mask] = 1.0 / total[mask]
    increase = np.hstack((y_help[:, 0:1], np.diff(y_help)))
    below_size = total - stack
    below_size += 0.5 * y_help
    move_up = below_size * inv_total
    move_up[:, 0] = 0.5
    center = (move_up - 0.5) * increase
    center = np.cumsum(center.sum(0))
    first_line = center - 0.5 * total
    stack += first_line


for i, v in sorted_df.iterrows():
    txt_col = 'black' if sum(palette_full.get(v.role)) > 2 else 'white'
    ax.annotate(f'{v["name"]} ({v.abbr})', [float(v.start)+0.03, stack[i][(int(v.start)-1940)*4]-0.6], fontsize = 10, color = txt_col, zorder = 20, 
                #fontname = 'DIN Condensed'
                 font = font_library.RobotoCondensed_Light,
                 #font = test_font
                 )

ax.legend(handles = legend_elements_full, 
          loc='lower left', 
          #bbox_to_anchor=(1, 0.5)
          frameon = False,
          fontsize = 'XX-large',
          prop = font_library.Roboto_Regular,
          title = 'Funktion',
          title_fontproperties = font_library.Roboto_Black
          #title_fontsize = 12,
          #title_alignment = 'left'
          #prop = test_font
          )
ax.set_facecolor('whitesmoke')
ax.vlines(np.arange(1945,2025,5), ymin=-30, ymax=30, color="black", alpha = 0.6, linestyles= (0, (5, 10)), zorder = 0 )
#ax.vlines([1943,1944,2025,2026], ymin=-30, ymax=30, color="red") ## uncomment to validate years
plt.xticks(ticks = np.arange(1945,2025,5), labels=  [str(x) for x in np.arange(1945, 2025, 5)], rotation = 90)
ax.tick_params(top=False, labeltop=True, bottom=False, labelbottom=True, pad = -60)
ax.set(frame_on=False)
plt.yticks([])
plt.xticks(font = font_library.Roboto_Regular
           #font = test_font
           )
plt.title('STAFF 1943-2025', font=font_library.Roboto_Black, fontsize = 120, color = '#006FB9', pad = 150)
#plt.savefig('wiggle.pdf', 
#            backend = 'cairo',
#            dpi = 300
#            )
plt.show()

In [20]:
font_library.clear_library()